In [1]:
%matplotlib inline
%load_ext autoreload
%autoreload 2

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from IPython.display import Markdown, display, HTML
from collections import defaultdict

import torch
import torch.nn as nn
import torch.optim as optim
from livelossplot import PlotLosses

# Fix the dying kernel problem (only a problem in some installations - you can remove it, if it works without it)
import os
os.environ['KMP_DUPLICATE_LIB_OK'] = 'True'

# Load the dataset for recommenders

In [2]:
data_path = os.path.join("data", "hotel_data")

interactions_df = pd.read_csv(os.path.join(data_path, "hotel_data_interactions_df.csv"), index_col=0)

base_item_features = ['term', 'length_of_stay_bucket', 'rate_plan', 'room_segment', 'n_people_bucket', 'weekend_stay']

column_values_dict = {
    'term': ['WinterVacation', 'Easter', 'OffSeason', 'HighSeason', 'LowSeason', 'MayLongWeekend', 'NewYear', 'Christmas'],
    'length_of_stay_bucket': ['[0-1]', '[2-3]', '[4-7]', '[8-inf]'],
    'rate_plan': ['Standard', 'Nonref'],
    'room_segment': ['[0-160]', '[160-260]', '[260-360]', '[360-500]', '[500-900]'],
    'n_people_bucket': ['[1-1]', '[2-2]', '[3-4]', '[5-inf]'],
    'weekend_stay': ['True', 'False']
}

interactions_df.loc[:, 'term'] = pd.Categorical(
    interactions_df['term'], categories=column_values_dict['term'])
interactions_df.loc[:, 'length_of_stay_bucket'] = pd.Categorical(
    interactions_df['length_of_stay_bucket'], categories=column_values_dict['length_of_stay_bucket'])
interactions_df.loc[:, 'rate_plan'] = pd.Categorical(
    interactions_df['rate_plan'], categories=column_values_dict['rate_plan'])
interactions_df.loc[:, 'room_segment'] = pd.Categorical(
    interactions_df['room_segment'], categories=column_values_dict['room_segment'])
interactions_df.loc[:, 'n_people_bucket'] = pd.Categorical(
    interactions_df['n_people_bucket'], categories=column_values_dict['n_people_bucket'])
interactions_df.loc[:, 'weekend_stay'] = interactions_df['weekend_stay'].astype('str')
interactions_df.loc[:, 'weekend_stay'] = pd.Categorical(
    interactions_df['weekend_stay'], categories=column_values_dict['weekend_stay'])

display(HTML(interactions_df.head(15).to_html()))

# (Optional) Prepare numerical user features

The method below is left here for convenience if you want to experiment with content-based user features as an input for your neural network.

In [3]:
def n_to_p(l):
    n = sum(l)
    return [x / n for x in l] if n > 0 else l

def calculate_p(x, values):
    counts = [0]*len(values)
    for v in x:
        counts[values.index(v)] += 1

    return n_to_p(counts)

def prepare_users_df(interactions_df):
    ######################
    # this function returns dataframe with float values based on number
    # of times user interacted with item with said feature
    ######################
    users_df = interactions_df.copy()
    #this line is to narrow number of used features
    
#     users_df = users_df.loc[:,["user_id","term","length_of_stay_bucket","n_people_bucket", "room_segment"]]
#     users_df = users_df.loc[:,["user_id","term", "room_segment"]]

    users_df = pd.get_dummies(users_df)
    users_df = users_df.loc[:,users_df.columns != "item_id"]
    users_df = users_df.groupby(['user_id']).sum()

    users_df = users_df / users_df.sum(axis=1).values.reshape(-1, 1)
    users_df = users_df.add_prefix('user_')
    users_df = users_df.rename_axis(None, axis=1).fillna(0).reset_index()
    user_features = users_df.loc[:,users_df.columns != "user_id"].columns.to_list()
    
    
    
    return users_df, user_features
    

users_df, user_features = prepare_users_df(interactions_df)

print(user_features)

display(HTML(users_df.loc[users_df['user_id'].isin([706, 1736, 7779, 96, 1, 50, 115])].head(15).to_html()))

['user_term_WinterVacation', 'user_term_Easter', 'user_term_OffSeason', 'user_term_HighSeason', 'user_term_LowSeason', 'user_term_MayLongWeekend', 'user_term_NewYear', 'user_term_Christmas', 'user_length_of_stay_bucket_[0-1]', 'user_length_of_stay_bucket_[2-3]', 'user_length_of_stay_bucket_[4-7]', 'user_length_of_stay_bucket_[8-inf]', 'user_rate_plan_Standard', 'user_rate_plan_Nonref', 'user_room_segment_[0-160]', 'user_room_segment_[160-260]', 'user_room_segment_[260-360]', 'user_room_segment_[360-500]', 'user_room_segment_[500-900]', 'user_n_people_bucket_[1-1]', 'user_n_people_bucket_[2-2]', 'user_n_people_bucket_[3-4]', 'user_n_people_bucket_[5-inf]', 'user_weekend_stay_True', 'user_weekend_stay_False']


# (Optional) Prepare numerical item features

The method below is left here for convenience if you want to experiment with content-based item features as an input for your neural network.

# Neural network recommender

<span style="color:red"><font size="4">**Task:**</font></span><br> 
Code a recommender based on a neural network model. You are free to choose any network architecture you find appropriate. The network can use the interaction vectors for users and items, embeddings of users and items, as well as user and item features (you can use the features you developed in the first project).

Remember to keep control over randomness - in the init method add the seed as a parameter and initialize the random seed generator with that seed (both for numpy and pytorch):

```python
self.seed = seed
self.rng = np.random.RandomState(seed=seed)
```
in the network model:
```python
self.seed = torch.manual_seed(seed)
```

You are encouraged to experiment with:
  - the number of layers in the network, the number of neurons and different activation functions,
  - different optimizers and their parameters,
  - batch size and the number of epochs,
  - embedding layers,
  - content-based features of both users and items.

In [38]:
def map_items_to_onehot(df):
    one_hot = pd.get_dummies(df.loc[:, base_item_features])
    df = df.drop(base_item_features, axis = 1)
    df = df.join(one_hot)
    
    return df, list(one_hot.columns)

def prepare_items_df(interactions_df):
    items_df = interactions_df.loc[:, ["item_id"] + base_item_features].drop_duplicates()
    
    items_df, item_features = map_items_to_onehot(items_df)
    
    return items_df, item_features


items_df, item_features = prepare_items_df(interactions_df)

print(item_features)

x = items_df.loc[items_df['item_id'] == 760]
x = x
display(x)

['term_WinterVacation', 'term_Easter', 'term_OffSeason', 'term_HighSeason', 'term_LowSeason', 'term_MayLongWeekend', 'term_NewYear', 'term_Christmas', 'length_of_stay_bucket_[0-1]', 'length_of_stay_bucket_[2-3]', 'length_of_stay_bucket_[4-7]', 'length_of_stay_bucket_[8-inf]', 'rate_plan_Standard', 'rate_plan_Nonref', 'room_segment_[0-160]', 'room_segment_[160-260]', 'room_segment_[260-360]', 'room_segment_[360-500]', 'room_segment_[500-900]', 'n_people_bucket_[1-1]', 'n_people_bucket_[2-2]', 'n_people_bucket_[3-4]', 'n_people_bucket_[5-inf]', 'weekend_stay_True', 'weekend_stay_False']


array([[0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 1, 0, 0, 1, 0, 0, 0, 1, 0, 0,
        0, 0, 1]], dtype=uint8)

In [63]:
from recommenders.recommender import Recommender


class Net(nn.Module):
    def __init__(self,seed, e_u, e_i):
        super(Net, self).__init__()
        self.seed = torch.manual_seed(seed)

        self.embedding = nn.Embedding(e_u, 25)

    def forward(self, x):
        user_id = x[0]
        item_repr = x[1]
        
        y = self.embedding(user_id) * item_repr
        y = torch.sum(y)
        y = torch.sigmoid(y)

        return y

class NNRecommender(Recommender):
    """
    Linear recommender class based on user and item features.
    """
    
    def __init__(self, seed=6789, n_neg_per_pos=5, lr=0.01, ):
        """
        Initialize recommender params and variables.
        """
        self.model = None
        self.n_neg_per_pos = n_neg_per_pos
        
        self.recommender_df = pd.DataFrame(columns=['user_id', 'item_id', 'score'])
        self.users_df = None
        self.user_features = None
        
        self.seed = seed
        self.rng = np.random.RandomState(seed=seed)
        
        # You can add more arguments if needed
        # <<<Write your code here>>>
        self.most_popular_items = None
        self.n_epochs = 1000
        self.lr = lr
    
    def fit(self, interactions_df, users_df, items_df):
        """
        Training of the recommender.
        
        :param pd.DataFrame interactions_df: DataFrame with recorded interactions between users and items 
            defined by user_id, item_id and features of the interaction.
        :param pd.DataFrame users_df: DataFrame with users and their features defined by user_id and the user feature columns.
        :param pd.DataFrame items_df: DataFrame with items and their features defined by item_id and the item feature columns.
        """
        
        interactions_df = interactions_df.copy()
        n_users = np.max(interactions_df['user_id']) + 1
        n_items = np.max(interactions_df['item_id']) + 1
        
        r = np.zeros(shape=(n_users, n_items))
        for idx, interaction in interactions_df.iterrows():
            r[int(interaction['user_id'])][int(interaction['item_id'])] = 1

        
        
        # Prepare users_df and items_df 
        # (optional - use only if you want to train a hybrid model with content-based features)
        
        users_df, user_features = prepare_users_df(interactions_df)
        
        self.users_df = users_df
        self.user_features = user_features
        
        items_df, item_features = prepare_items_df(interactions_df)
        items_df = items_df.loc[:, ['item_id'] + item_features]
        
        # Generate negative interactions
        
        # <<<Write your code here>>>
        
        negative_interactions = []
       
        i = 0
        while i < self.n_neg_per_pos * len(interactions_df):
            sample_size = 1000
            user_ids = self.rng.choice(np.arange(n_users), size=sample_size)
            item_ids = self.rng.choice(np.arange(n_items), size=sample_size)

            j = 0
            while j < sample_size and i < self.n_neg_per_pos * len(interactions_df):
                if r[user_ids[j]][item_ids[j]] == 0:
                    negative_interactions.append([user_ids[j], item_ids[j], 0])
                    i += 1
                j += 1
        
        interactions_df = pd.concat(
            [interactions_df, pd.DataFrame(negative_interactions, columns=['user_id', 'item_id', 'interacted'])])
        
        # Merge user and item features
        # (optional - use only if you want to train a hybrid model with content-based features)
        
        interactions_df = pd.merge(interactions_df, users_df, on=['user_id'])
        interactions_df = pd.merge(interactions_df, items_df, on=['item_id'])

        # Initialize the neural network model
        
        # <<<Write your code here>>>
        
        
#         user_repr = self.rng.normal(0, 1, size=(r.shape[0], len(interactions_df)))
#         item_repr = self.rng.normal(0, 1, size=(r.shape[1], len(interactions_df)))
        
#         self.model = Net(self.seed,len(interactions_df))
        self.model = Net(self.seed,n_users, n_items)
        
        # Train the model using an optimizer
        interaction_ids = self.rng.permutation(len(interactions_df)).astype(int)

        
        # <<<Write your code here>>>
        optimizer = optim.SGD(self.model.parameters(), lr=self.lr)
        
        losses = []
        loss = 0
        data = []
        for epoch in range(self.n_epochs):
            optimizer.zero_grad()
            
            for i in interaction_ids:
                idx = int(i)
                user_id = torch.tensor(int(interactions_df.iloc[idx][0]))
                item_id = int(interactions_df.iloc[idx][1])
                
                x = items_df.loc[items_df['item_id'] == item_id]
                item_repr = torch.tensor(x.loc[:, items_df.columns != "item_id"].to_numpy())
                
                y = self.model((user_id, item_repr))
                
                loss += torch.pow(y - torch.tensor(r[user_id, item_id]), 2)
                
            
            loss.backward()
            losses.append(loss.item())
            optimizer.step()
        
        
        # most popular item
        interaction_count = interactions_df.loc[:, ['item_id', 'user_id']].groupby(by='item_id').count()
        interaction_count = interaction_count.sort_values('user_id', ascending=False)
        self.most_popular_items = interaction_count.index
    
    def recommend(self, users_df, items_df, n_recommendations=1):
        """
        Serving of recommendations. Scores items in items_df for each user in users_df and returns 
        top n_recommendations for each user.
        
        :param pd.DataFrame users_df: DataFrame with users and their features for which recommendations should be generated.
        :param pd.DataFrame items_df: DataFrame with items and their features which should be scored.
        :param int n_recommendations: Number of recommendations to be returned for each user.
        :return: DataFrame with user_id, item_id and score as columns returning n_recommendations top recommendations 
            for each user.
        :rtype: pd.DataFrame
        """
        
        # Clean previous recommendations (iloc could be used alternatively)
        self.recommender_df = self.recommender_df[:0]
        
        # Prepare users_df and items_df
        # (optional - use only if you want to train a hybrid model with content-based features)
        
        users_df = users_df.loc[:, 'user_id']
        users_df = pd.merge(users_df, self.users_df, on=['user_id'], how='left').fillna(0)
        
        items_df, item_features = prepare_items_df(items_df)
        items_df = items_df.loc[:, ['item_id'] + item_features]
        
        # Score the items
    
        recommendations = pd.DataFrame(columns=['user_id', 'item_id', 'score'])
        
        for ix, user in users_df.iterrows():
            
            # Calculate the score for the user and every item in items_df
            # <<<Write your code here>>>
            
            scores = []

            user_id = user['user_id']

            if user_id in self.users_df:

                ids_list = items_df['item_id'].tolist()
                id_to_pos = np.array([0]*len(ids_list))
                for k in range(len(ids_list)):
                    id_to_pos[ids_list[k]] = k
                scores = np.matmul(self.user_repr[mapped_user_id].reshape(1, -1),
                                   self.item_repr[ids_list].T).flatten()

                # Choose n recommendations based on highest scores
                if not self.should_recommend_already_bought:
                    x_list = self.interactions_df.loc[
                        self.interactions_df['user_id'] == mapped_user_id]['item_id'].tolist()
                    scores[id_to_pos[x_list]] = -1e100

                chosen_pos = np.argsort(-scores)[:n_recommendations]

                for item_pos in chosen_pos:
                    recommendations.append(
                        {
                            'user_id': user_id,
                            'item_id': id_list[item_pos],
                            'score': scores[item_pos]
                        }
                    )
            else:  # For new users recommend most popular items
                for i in range(n_recommendations):
                    recommendations.append(
                        {
                            'user_id': user['user_id'],
                            'item_id': self.most_popular_items[i],
                            'score': 1.0
                        }
                    )
            
            chosen_ids = np.argsort(-scores)[:n_recommendations]
            
            recommendations = []
            for item_id in chosen_ids:
                recommendations.append(
                    {
                        'user_id': user['user_id'],
                        'item_id': item_id,
                        'score': scores[item_id]
                    }
                )
            
            user_recommendations = pd.DataFrame(recommendations)

            self.recommender_df = pd.concat([self.recommender_df, user_recommendations])

        return self.recommender_df

# Quick test of the recommender

In [64]:
items_df = interactions_df.loc[:, ['item_id'] + base_item_features].drop_duplicates()
user_id = interactions_df.iloc[1]

In [ ]:
# Fit method
nn_recommender = NNRecommender()
nn_recommender.fit(interactions_df, None, None)

tensor(0.0065, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(0.0208, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(0.0235, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(0.4238, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(1.1919, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(1.2002, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(1.7941, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(2.1869, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(3.0182, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(3.0714, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(3.3582, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(3.3848, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(3.4890, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(3.8944, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(4.8507, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(5.6071, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(5.6089, dtype=torch.float64, grad

tensor(59.7714, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(60.3852, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(60.4534, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(60.5049, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(60.5374, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(61.3593, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(61.3852, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(61.5495, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(62.0693, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(62.7049, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(62.8095, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(63.2594, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(64.2104, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(64.2364, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(64.6114, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(65.5528, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(65.5994, dtype=to

tensor(110.3060, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(111.1880, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(111.8432, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(111.8543, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(112.0546, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(112.2472, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(112.3039, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(112.3047, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(113.2273, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(113.7030, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(114.6921, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(114.7645, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(114.8251, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(114.8283, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(115.1645, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(116.1522, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(1

tensor(156.9307, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(157.8082, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(157.9343, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(158.6046, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(159.5773, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(159.6095, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(159.6535, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(160.0230, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(160.0468, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(160.9659, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(161.0124, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(161.3210, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(162.0426, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(162.0478, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(162.1475, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(163.1094, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(1

tensor(213.3252, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(214.0502, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(214.1213, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(215.0950, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(215.9694, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(216.4521, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(216.4522, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(216.5472, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(217.0908, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(217.0908, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(217.1433, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(217.1544, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(217.6178, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(217.6590, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(218.4697, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(218.5198, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(2

...

tensor(31757.8507, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31757.8507, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31757.8742, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31758.6445, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31758.8099, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31759.6316, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31759.8186, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31759.8222, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31760.6021, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31761.5783, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31761.8945, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31762.8779, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31762.8780, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31763.3612, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31764.2898, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31764.2910, dtype=torch.float64, 

tensor(31811.3463, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31812.3187, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31812.8991, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31813.1616, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31814.0166, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31814.6639, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31814.6675, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31814.8165, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31814.8168, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31815.3969, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31816.0410, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31816.0568, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31816.0675, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31816.3473, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31816.4652, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31817.0243, dtype=torch.float64, 

tensor(31874.2561, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31874.3792, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31874.9904, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31874.9914, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31875.7989, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31876.3107, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31876.7086, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31876.9703, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31877.0443, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31877.0469, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31877.1375, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31878.1131, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31878.2414, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31878.7522, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31879.1536, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31879.7592, dtype=torch.float64, 

tensor(31934.5526, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31934.5631, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31934.6814, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31934.7059, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31935.4902, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31936.4584, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31936.4590, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31936.7750, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31937.7135, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31937.7166, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31938.6966, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31939.4924, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31940.1120, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31940.4024, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31941.2841, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31942.0151, dtype=torch.float64, 

tensor(31990.7980, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31991.6477, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31992.0854, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31992.1491, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31992.3620, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31993.0277, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31993.2722, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31993.9349, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31994.7382, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31994.8164, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31995.6801, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31996.0694, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31996.7187, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31997.5178, dtype=torch.float64, grad_fn=<AddBackward0>)
tensor(31997.5178, dtype=torch.float64, grad_fn=<AddBackward0>)


In [ ]:
# Recommender method

recommendations = nn_recommender.recommend(pd.DataFrame([[1], [2], [3], [4], [5]], columns=['user_id']), items_df, 10)

recommendations = pd.merge(recommendations, items_df, on='item_id', how='left')
display(HTML(recommendations.to_html()))

# Tuning method

In [ ]:
from evaluation_and_testing.testing import evaluate_train_test_split_implicit

seed = 6789

In [ ]:
from hyperopt import hp, fmin, tpe, Trials
import traceback

def tune_recommender(recommender_class, interactions_df, items_df, 
                     param_space, max_evals=1, show_progressbar=True, seed=6789):
    # Split into train_validation and test sets

    shuffle = np.arange(len(interactions_df))
    rng = np.random.RandomState(seed=seed)
    rng.shuffle(shuffle)
    shuffle = list(shuffle)

    train_test_split = 0.8
    split_index = int(len(interactions_df) * train_test_split)

    train_validation = interactions_df.iloc[shuffle[:split_index]]
    test = interactions_df.iloc[shuffle[split_index:]]

    # Tune

    def loss(tuned_params):
        recommender = recommender_class(seed=seed, **tuned_params)
        hr1, hr3, hr5, hr10, ndcg1, ndcg3, ndcg5, ndcg10 = evaluate_train_test_split_implicit(
            recommender, train_validation, items_df, seed=seed)
        return -hr10

    n_tries = 1
    succeded = False
    try_id = 0
    while not succeded and try_id < n_tries:
        try:
            trials = Trials()
            best_param_set = fmin(loss, space=param_space, algo=tpe.suggest, 
                                  max_evals=max_evals, show_progressbar=show_progressbar, trials=trials, verbose=True)
            succeded = True
        except:
            traceback.print_exc()
            try_id += 1
            
    if not succeded:
        return None
        
    # Validate
    
    recommender = recommender_class(seed=seed, **best_param_set)

    results = [[recommender_class.__name__] + list(evaluate_train_test_split_implicit(
        recommender, {'train': train_validation, 'test': test}, items_df, seed=seed))]

    results = pd.DataFrame(results, 
                           columns=['Recommender', 'HR@1', 'HR@3', 'HR@5', 'HR@10', 'NDCG@1', 'NDCG@3', 'NDCG@5', 'NDCG@10'])

    display(HTML(results.to_html()))
    
    return best_param_set

## Tuning of the recommender

<span style="color:red"><font size="4">**Task:**</font></span><br> 
Tune your model using the code below. You only need to put the class name of your recommender and choose an appropriate parameter space.

In [ ]:
param_space = {
    'n_neg_per_pos': hp.quniform('n_neg_per_pos', 1, 10, 1)
}

best_param_set = tune_recommender(NNRecommender, interactions_df, items_df,
                                  param_space, max_evals=10, show_progressbar=True, seed=seed)

print("Best parameters:")
print(best_param_set)

# Final evaluation

<span style="color:red"><font size="4">**Task:**</font></span><br> 
Run the final evaluation of your recommender and present its results against the Amazon and Netflix recommenders' results. You just need to give the class name of your recommender and its tuned parameters below.

It's optional, but for better effect you can include here the results from all recommenders created during in this class.

In [ ]:
nn_recommender = NNRecommender(n_neg_per_pos=1)  # Initialize your recommender here

# Give the name of your recommender in the line below
nn_tts_results = [['NNRecommender'] + list(evaluate_train_test_split_implicit(
    nn_recommender, interactions_df, items_df))]

nn_tts_results = pd.DataFrame(
    nn_tts_results, columns=['Recommender', 'HR@1', 'HR@3', 'HR@5', 'HR@10', 'NDCG@1', 'NDCG@3', 'NDCG@5', 'NDCG@10'])

display(HTML(nn_tts_results.to_html()))

In [ ]:
from recommenders.amazon_recommender import AmazonRecommender

amazon_recommender = AmazonRecommender()

amazon_tts_results = [['AmazonRecommender'] + list(evaluate_train_test_split_implicit(
    amazon_recommender, interactions_df, items_df))]

amazon_tts_results = pd.DataFrame(
    amazon_tts_results, columns=['Recommender', 'HR@1', 'HR@3', 'HR@5', 'HR@10', 'NDCG@1', 'NDCG@3', 'NDCG@5', 'NDCG@10'])

display(HTML(amazon_tts_results.to_html()))

In [ ]:
from recommenders.netflix_recommender import NetflixRecommender

netflix_recommender = NetflixRecommender(embedding_dim=8, n_epochs=200, print_type='live')

netflix_tts_results = [['NetflixRecommender'] + list(evaluate_train_test_split_implicit(
    netflix_recommender, interactions_df, items_df))]

netflix_tts_results = pd.DataFrame(
    netflix_tts_results, columns=['Recommender', 'HR@1', 'HR@3', 'HR@5', 'HR@10', 'NDCG@1', 'NDCG@3', 'NDCG@5', 'NDCG@10'])

display(HTML(netflix_tts_results.to_html()))

In [ ]:
tts_results = pd.concat([nn_tts_results, amazon_tts_results, netflix_tts_results]).reset_index(drop=True)
display(HTML(tts_results.to_html()))

# Summary

<span style="color:red"><font size="4">**Task:**</font></span><br> 
Write a summary of your experiments. What worked well and what did not? What are your thoughts how could you possibly further improve the model?